# Question Answering System
**Subject: Natural Language Processing**

**Subject Code:TNL 3221**

**Group: 13**

**Member:**

Lee Ting Wei 1181203031

Loo Chze Xin 1181203185

Ong Jia Xiang 1181202342

Lim Shueh Ting 1201300175


**Install Necassary Library**

In [1]:
%%bash

pip install --upgrade pip
pip install farm-haystack[colab,inmemorygraph]==1.16.0

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 713.1/713.1 kB 17.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 299.9/299.9 kB 29.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 11.2 MB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.8/236.8 kB 22.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 68.0/68.0 kB 8.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 45.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.7/10.7 MB 60.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 8.4 MB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing met

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
tensorflow 2.12.0 requires protobuf!=4.21.0,!=4.21.1,!=4.21.2,!=4.21.3,!=4.21.4,!=4.21.5,<5.0.0dev,>=3.20.3, but you have protobuf 3.20.2 which is incompatible.
tensorflow-metadata 1.13.1 requires protobuf<5,>=3.20.3, but you have protobuf 3.20.2 which is incompatible.


**Import Logging for Debug**

In [1]:
import logging

logging.basicConfig(format="%(levelname)s - %(name)s -  %(message)s", level=logging.WARNING)
logging.getLogger("haystack").setLevel(logging.INFO)


**Import Necassary Library**

In [2]:
from haystack.document_stores.memory import InMemoryDocumentStore
from haystack.nodes import TfidfRetriever, FARMReader
from haystack.utils import print_answers

**Mount Google Drive**

In [3]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


**Load Knowledge Graph in Pickle File**

In [4]:
import pickle

pickle_file = '/content/drive/MyDrive/Group13_NLP_Project/knowledge_graph.pickle'

# Load the knowledge graph from the pickle file
with open(pickle_file, 'rb') as f:
  knowledge_graph = pickle.load(f)

print("Knowledge graph loaded from ", pickle_file)

Knowledge graph loaded from  /content/drive/MyDrive/Group13_NLP_Project/knowledge_graph.pickle


In [5]:
print("Nodes:", knowledge_graph.nodes())
print("Edges:", knowledge_graph.edges())

Nodes: ['Daripada', 'Wikipedia', ',', 'ensiklopedia', 'bebas', None, 'Nuvola', 'Malaysian', 'flag', 'svg', 'Hidup', 'Malaysia', 'Budaya', 'Masakan', 'Demografi', 'Ekonomi', 'Didik', 'Kumpul', 'etnik', 'Filem', 'Kesihatan', 'Cuti', 'Bahasa', 'Sastera', 'Inggeris', 'Muzik', 'Politik', 'Agama', 'Bebas', 'agama', 'Masyarakat', 'Sukan', 'Angkut', 'Lancong', 'lbs', 'Menara', 'Kembar', 'Petronas', 'Kuala', 'Lumpur', 'Pantai', 'Teluk', 'Cempedak', 'Antan', 'Selatan', 'Henti', 'Besar', 'Pandang', 'burung', 'Kuching', 'Sarawak', 'duduk', 'ke9', 'dunia', 'tiba', 'lancong', '1', 'Lapor', 'Daya', 'Saing', '2017', 'ke25', '141', 'negara', 'baik', 'Asia', 'Dalam', 'usaha', 'pelbagai', 'ekonomi', 'jadi', 'gantung', 'eksport', 'raja', 'tolak', 'tingkat', 'Akibat', 'sumber', 'dapat', 'tukar', 'asing', 'tiga', 'besar', '2', 'sumbang', '7', '2005', '3', 'Agens', 'bertanggungjawab', 'promosi', 'Tourism', 'Lembaga', 'Gala', 'MTPB', 'Pada', '20', 'Mei', '1987', 'Menteri', 'Seni', 'MOCAT', 'tubuh', 'TDC', 'pi

**Create Document Store**

In [6]:
document_store = InMemoryDocumentStore()

INFO:haystack.modeling.utils:Using devices: CPU - Number of GPUs: 0


In [7]:
node_sentences = {}
documents = []
nodes = [node for node in knowledge_graph.nodes() if node is not None]

for node in nodes:
  # Get all the edges related to the current node
  related_edges = [edge for edge in knowledge_graph.edges() if edge[0] == node or edge[1] == node]

  # Get the parents and grandparents of the current node
  parents = [edge[0] for edge in related_edges if edge[1] == node]
  grandparents = []
  for parent in parents:
    grandparents.extend([edge[0] for edge in related_edges if edge[1] == parent])

  # Get the children and grandchildren of the current node
  children = [edge[1] for edge in related_edges if edge[0] == node]
  grandchildren = []
  for child in children:
    grandchildren.extend([edge[1] for edge in related_edges if edge[0] == child])

  # Create the sentence by combining all the related nodes
  sentence_parts = grandparents + parents + [node] + children + grandchildren
  sentence = ' '.join(sentence_parts)

  # Store the sentence for the current node
  node_sentences[node] = sentence

  # Create the document with the node and the sentence as the content
  documents.append({'text': node, 'content': sentence})

In [8]:
#Write the knowledge graph in document store
document_store.write_documents(documents)

INFO:haystack.document_stores.base:Duplicate Documents: Document with id '8e1da3e57e1f775209c4a1f49e8475d7' already exists in index 'document'
INFO:haystack.document_stores.base:Duplicate Documents: Document with id '23ad232f1682b9b49ba99feced8a8309' already exists in index 'document'
INFO:haystack.document_stores.base:Duplicate Documents: Document with id 'e4764b1b670827a4a94eca7ccc2620e9' already exists in index 'document'
INFO:haystack.document_stores.base:Duplicate Documents: Document with id '2d67e80574cb427d22eb5c99f71120a0' already exists in index 'document'
INFO:haystack.document_stores.base:Duplicate Documents: Document with id 'f1bb61511f4bb21fbec7d7cfc2df75b3' already exists in index 'document'
INFO:haystack.document_stores.base:Duplicate Documents: Document with id '912736ec3ddbf54ce13063663d825526' already exists in index 'document'
INFO:haystack.document_stores.base:Duplicate Documents: Document with id '8102c958b67babd2229c188924907936' already exists in index 'document'

In [9]:
#Initialize the retriever
retriever = TfidfRetriever(document_store=document_store)

INFO:haystack.nodes.retriever.sparse:Found 15857 candidate paragraphs from 15857 docs in DB


In [10]:
#Initialize the reader
model_name = "primasr/multilingualbert-for-eqa-finetuned"
reader = FARMReader(model_name_or_path=model_name, use_gpu=False)

INFO:haystack.modeling.utils:Using devices: CPU - Number of GPUs: 0
INFO:haystack.modeling.utils:Using devices: CPU - Number of GPUs: 0
INFO:haystack.modeling.model.language_model: * LOADING MODEL: 'primasr/multilingualbert-for-eqa-finetuned' (DebertaV2)
/usr/local/lib/python3.10/dist-packages/torch/_utils.py:776: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
INFO:haystack.modeling.model.language_model:Auto-detected model language: multilingual
INFO:haystack.modeling.model.language_model:Loaded 'primasr/multilingualbert-for-eqa-finetuned' (DebertaV2 model) from model hub.
INFO:haystack.modeling.utils:Using devices: CPU - Number of GPUs: 0


In [11]:
#Create pipeline with the component of retriever and reader
from haystack.pipelines import Pipeline
pipeline = Pipeline()
pipeline.add_node(component=retriever, name="Retriever", inputs=["Query"])
pipeline.add_node(component=reader, name="Reader", inputs=["Retriever"])

In [12]:
#Ask question and inferencing 5 results
question = "Negeri manakah yang terdapat Pulau?"
result = pipeline.run(query=question,params={
        "Retriever": {"top_k": 5},
        "Reader": {"top_k": 5}
    })

Inferencing Samples:   0%|          | 0/1 [00:00<?, ? Batches/s]

In [13]:
#Take a look on the inferencing result
from pprint import pprint

pprint(result)

{'answers': [<Answer {'answer': 'Pulau Langkawi', 'type': 'extractive', 'score': 0.9998382329940796, 'context': 'mah bahagian rehat keluarga lengkap tawar pandang Antara pulau feri Pulau Langkawi Melaka kenal Di aktivitiaktiviti 16 pusat simpan samping panorama c', 'offsets_in_document': [{'start': 3116, 'end': 3130}], 'offsets_in_context': [{'start': 68, 'end': 82}], 'document_ids': ['db2d4a34a03e819205daf2d36ac2e877'], 'meta': {'text': 'Pulau'}}>,
             <Answer {'answer': 'Pulau Tawan Kinabalu', 'type': 'extractive', 'score': 0.9998331665992737, 'context': 'Pulau Tawan Kinabalu Yang', 'offsets_in_document': [{'start': 0, 'end': 20}], 'offsets_in_context': [{'start': 0, 'end': 20}], 'document_ids': ['3256d3b02ed9b4dd2ba3c5eb2456b711'], 'meta': {'text': 'Tawan'}}>,
             <Answer {'answer': 'Malang', 'type': 'extractive', 'score': 0.9996744394302368, 'context': 'awan Kapas panggil Permata myrulee anwarudinrazali berjalanjalan credit Malang Pulau Pulau Pulau Pulau Pulau Pul

In [14]:
#Set the first prior answer to answer user
i=0

retrieved_main_answer = result['answers'][i].answer
retrieved_main_context = result['answers'][i].context

In [15]:
#Finalize answer
final_answer = retrieved_main_answer + ", " + retrieved_main_context
final_answer

'Pulau Langkawi, mah bahagian rehat keluarga lengkap tawar pandang Antara pulau feri Pulau Langkawi Melaka kenal Di aktivitiaktiviti 16 pusat simpan samping panorama c'

**Install Necassary Library for Chatbot**

In [5]:
!pip install gradio

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.0/20.0 MB 50.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 46.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.0/57.0 kB 5.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 288.3/288.3 kB 22.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.4/75.4 kB 8.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.5/50.5 kB 6.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 137.0/137.0 kB 12.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.7/45.7 kB 4.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 6.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.9/129.9 kB 14.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 k

In [6]:
!pip install langdetect

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 981.5/981.5 kB 19.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for langdetect: filename=langdetect-1.0.9-py3-none-any.whl size=993224 sha256=be566de8058d54a5f0e7078bc0a168fac0e9e84cb983fdbf5bb74f77666b9227
  Stored in directory: /root/.cache/pip/wheels/95/03/7d/59ea870c70ce4e5a370638b5462a7711ab78fba2f655d05106
Successfully built langdetect


In [7]:
!pip install git+https://github.com/huggingface/transformers.git
!pip install git+https://github.com/huggingface/datasets.git
!pip install sacrebleu sentencepiece

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/huggingface/transformers.git to /tmp/pip-req-build-c_3yu8ko
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/transformers.git /tmp/pip-req-build-c_3yu8ko
  Resolved https://github.com/huggingface/transformers.git to commit 695928e1e573e5a9953ad540c0f8345767348feb
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 18.7 MB/s eta 0:00:00
  Created wheel for transformers: filename=transformers-4.31.0.dev0-py3-none-any.whl size=7171321 sha256=1fea11794f13a899cfe9c6e6b3355cafa9ed14685261a324e9a91a76908b558d
  Stored in directory: /tmp/pip-ephem-wheel-cache-5jwau5ps/wheels/e7/9c/5b/e1a9c8007c343041e61cc484433d512ea9274272e3fcbe7c16
Successfully built transformers
  Attempting uninstall: trans

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/huggingface/datasets.git to /tmp/pip-req-build-n5wosx19
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/datasets.git /tmp/pip-req-build-n5wosx19
  Resolved https://github.com/huggingface/datasets.git to commit 963ff6de6eae80a6de4aabf0092eb3dfbe43096e
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.5/212.5 kB 8.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 14.1 MB/s eta 0:00:00
  Created wheel for datasets: filename=datasets-2.12.1.dev0-py3-none-any.whl size=481779 sha256=9b643a125cdf7c130571ed2a2a95e5705050bafdf6fc22a5f065850034340052
  Stored in directory: /tmp/pip-ephem-wheel-cache-67vuvo1b/wheels/57/f4/c4/53c677af89fec0ef3226c1e75a38367b37c2fa626f0544d3e4

**Language Detection**

In [16]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM
# Targeted to Translate English queries to Malay Language
# Initialize the tokenizer
en_id_tokenizer = AutoTokenizer.from_pretrained("Helsinki-NLP/opus-mt-en-id")
# Initialize the model
en_id_model = AutoModelForSeq2SeqLM.from_pretrained("Helsinki-NLP/opus-mt-en-id")

/usr/local/lib/python3.10/dist-packages/transformers/models/marian/tokenization_marian.py:194: UserWarning: Recommended: pip install sacremoses.
  warnings.warn("Recommended: pip install sacremoses.")


In [17]:
# Targeted to Translate Malay Answer to English Language
# Initialize the tokenizer
id_en_tokenizer = AutoTokenizer.from_pretrained("Helsinki-NLP/opus-mt-id-en")
# Initialize the model
id_en_model = AutoModelForSeq2SeqLM.from_pretrained("Helsinki-NLP/opus-mt-id-en")

**ChatBot Function**

In [18]:
#Defined some pairs for chatbot response
pairs = [
    [
        "your answer is wrong",
        "Sorry for providing wrong answer, here is the newest answer:\n\n",
        "I am sorry that I can't actually answer your question =("
    ],
    [
        "jawapan anda adalah salah",
        "Maaf sedangkan memberi jawapan yang salah. Berikut adalah jawapan yang baru:\n\n",
        "Minta Maaf, saya tidak boleh menemukan soalan anda =("
    ]]

In [19]:
#Function for checking reiterate providing answer for same question
def checkReiterateQuery(query,lang):
  if query in [pairs[0][0],pairs[1][0]]:
    if lang == 'en':
      j = 0
    else:
      j = 1
    return True, j

  else:
    return False , 3

In [20]:
import gradio as gr
from langdetect import detect
import warnings
warnings.filterwarnings('ignore')
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM


chat_history = []
answer_counter = 0
def chatbot_interface(message):
  global answer_counter
  global result

  # Append the current message to the chat history
  chat_history.append(message)
  lang = detect(message)
  reiterate, j = checkReiterateQuery(message, lang)

  #If user want to re-iterate the answer for same question
  if reiterate:
    answer_counter = answer_counter + 1
    if answer_counter < 5:
      retrieved_main_answer = pairs[j][1] + result['answers'][answer_counter].answer
      retrieved_main_context = result['answers'][answer_counter].context
    else:
      retrieved_main_answer = pairs[j][2]
      retrieved_main_context = ""
  else:
    answer_counter = 0
    #if language is english then convert it to malay language
    if lang == "en":
      tokenized_text = en_id_tokenizer.prepare_seq2seq_batch([message], return_tensors='pt')
      translation = en_id_model.generate(**tokenized_text)
      message = en_id_tokenizer.batch_decode(translation, skip_special_tokens=True)[0]

    result = pipeline.run(query=message.lower(), params={
            "Retriever": {"top_k": 5},
            "Reader": {"top_k": 5}})
    retrieved_main_answer = result['answers'][answer_counter].answer
    retrieved_main_context = result['answers'][answer_counter].context

  response = retrieved_main_answer + ", " + retrieved_main_context

  #Convert the response to english if user ask question in english
  if lang == "en":
    tokenized_text = id_en_tokenizer.prepare_seq2seq_batch([response.lower()], return_tensors='pt')
    translation = id_en_model.generate(**tokenized_text)
    response = id_en_tokenizer.batch_decode(translation, skip_special_tokens=True)[0]

  # Append the response to the chat history
  chat_history.append(response)

  # Join the chat history with newline characters
  chat_history_text = "\n\n".join(chat_history)

  return response, chat_history_text

# Create a Gradio interface
iface = gr.Interface(
    fn=chatbot_interface,
    inputs=gr.inputs.Textbox(label="Please Type Your Question Here: "),
    outputs=[gr.outputs.Textbox(label="Answers"), gr.outputs.Textbox(label="Chat History")],
    description="## Question Answering system\n\nIt supports **English** and **Bahasa Malaysia**.",
    allow_flagging = False
)

#Demo for the chatbot
iface.launch(share=True)

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
Running on public URL: https://cbfed45d3df70d2ba8.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)
